In [26]:
import requests, re, csv, pickle
import pandas as pd
import numpy as np
import pickle
import re

from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
init_notebook_mode()

In [24]:
class Wiki():
    api = "https://en.wikipedia.org/w/api.php"
    
    def __init__(self, category, 
                 no_views=False, 
                 no_content=False, 
                 custom_page_parser=None, 
                 extra_fields=None,
                 forbidden_categories_keywords=None):
        """
        custom_page_parser is for content mining. a function that given wiki text returns a dictionary of whatever it mined.
        Any extra fields need to be be added to extra_fields or to_csv will fail.
        """
        self.session = requests.Session()
        self.no_views = no_views
        self.no_content = no_content
        self.data = {}
        self.category = category
        self.category_cleaned = category.replace(' ','_').replace('Category:','')
        if custom_page_parser:
            self.custom_page_parser = custom_page_parser
        else:
            self.custom_page_parser = lambda text: {}
        if extra_fields:
            self.extra_fields = extra_fields
        else:
            self.extra_fields = []
        if forbidden_categories_keywords:
            self.forbidden_categories_keywords = forbidden_categories_keywords
        else:
            self.forbidden_categories_keywords = []
        
    def get(self, params):
        data = self.session.get(url=self.api, params=params).json()
        if 'continue' in data:
            params['cmcontinue'] = data['continue']['cmcontinue']
            t = list(data['query'].keys())[0]
            new_data = self.get(params)
            new_data['query'][t] = [*data['query'][t], *new_data['query'][t]]
            data = new_data
        return data
    
    def add_datum(self, data, cat):
        for d in data:
            name = d["title"]
            if name not in self.data:
                self.data[name] = d
                self.data[name]['category'] = cat
                if not self.no_views:
                    self.data[name]['views'] = self.get_pageviews(name)
                if not self.no_content:
                    wiki = self.get_content(name)
                    for key, value in self.custom_page_parser(wiki).items():
                        self.data[name][key] = value
            else:
                self.data[name]["category"] += '|' + cat
        
    def get_subcategories(self, cat):
        return [subcat for subcat in self.get_members(cat, 'subcat')
                       if all([k not in subcat['title'].lower() for k in self.forbidden_categories_keywords])]
    
    def get_pages(self,cat):
        return self.get_members(cat, 'page')
    
    def get_members(self, cat, cmtype='subcat|page'):
        params = {
            'action': "query",
            'list': "categorymembers",
            'cmtitle': cat,
            'cmtype': cmtype,
            'cmdir': "desc",
            'format': "json"
            }
        r = self.get(params)
        if 'query' not in r:
            print(f'{cat} replied with {str(r)}.')
            return []
        data = r['query']['categorymembers']
        self.add_datum(data, cat)
        return data
    
    def get_pages_recursively(self, cat=None):
        if cat is None:
            cat = self.category
        subcats = [s['title'] for s in self.get_subcategories(cat)]
        data = self.get_pages(cat)
        for c in subcats:
            ndata = self.get_pages_recursively(c)
            print(c, len(data),len(ndata))
            data.extend(ndata)
        return data
    
    def get_pageviews(self, page):
        url = f"https://wikimedia.org/api/rest_v1/metrics/pageviews/per-article/en.wikipedia/all-access/all-agents/{page.replace(' ','_')}/monthly/2018060100/2019060100"
        r = self.session.get(url).json()
        if 'items' in r:
            return sum([i['views'] for i in r['items']])/365
        else:
            print('error',page, r)
            return 'NA'
        
    def get_content(self,page):
        params = {
            'action': "query",
            'prop': 'revisions',
            'rvprop': 'content',
            'rvsection': 0,
            'titles': page,
            'format': "json"
            }
        data = self.session.get(url=self.api, params=params).json()
        pageid = list(data['query']['pages'].keys())[0]
        wikimarkup = data['query']['pages'][pageid]['revisions'][0]['*']
        return wikimarkup.encode('utf-8','ignore').decode('unicode_escape','ignore') #not quite right
    
    def to_csv(self):
        with open(f'{self.category_cleaned}.csv','w',newline='') as w:
            dw = csv.DictWriter(w,['title','category', 'ns','views','pageid']+self.extra_fields)
            dw.writeheader()
            dw.writerows(self.data.values())
        return self

## aircraft specific
class Planewiki(Wiki):
    """
    {|{{Infobox Aircraft Begin
     |name=A-132 TangarÃ¡
     |image =
     |caption=
    }}{{Infobox Aircraft Type
     |type=Primary trainer
     |national origin =[[Brazil]]
     |manufacturer=[[Embraer#Acquisition of Aerotec|Aerotec]]
     |first flight =26 February 1981
     |introduction=
     |retired =
     |status =
     |primary user=[[Bolivian Air Force]]
     |number built =7
     |developed from =Aerotec Uirapuru
    }}'''
    """
    
    def __init__(self, category, no_views=False, no_content=False):
        super().__init__(category, no_views=no_views, no_content=no_content,
                         custom_page_parser=self.plane_data,
                         extra_fields = ['first flight','number built','unit cost','introduction','retired','introduced','status'],
                         forbidden_categories_keywords=['airliner','9/11','deaths','organisation','ancident','iccident','squadron', 'fiction','film','novel','star wars','star trek'])
        #forbidden keywords have a title problem.
        

    def plane_data(self, wiki):
        data = {}
        for key in self.extra_fields:
            rex = re.search('\|'+key+'\s*\=\s*([^\n\|\<]+)',wiki)
            if rex:
                data[key] = rex.group(1).rstrip()
            else:
                data[key] = 'Error'
        return data


In [ ]:
# demo? try... Category:1980s Brazilian military aircraft
for title in ('Category:Cancelled aircraft projects','Category:Proposed_aircraft','Category:Military aircraft','Category:Civil aircraft'):
    plane = Planewiki(title)
    plane.get_pages_recursively()
    print('******',title, len(plane.data))
    plane.to_csv()
    pickle.dump(plane.data, open(f'{plane.category_cleaned}.p','wb'))

In [28]:
military = pickle.load(open('Military_aircraft.p','rb'))
civil = pickle.load(open('Civil_aircraft.p','rb'))

In [254]:
def get_built(txt):
    if isinstance(txt, float) or isinstance(txt, int):
        return txt
    elif isinstance(txt, str):
        txt_clean = txt.replace(',','').replace('.','')
        ## case 1. there are multiple xxxx: nnn
        rex = re.findall('.*?\:\s+(\d+)',txt_clean)
        if rex:
            n = 0
            for rexi in rex:
                n+=int(rexi)
            return n
        ## case 2.
        rex = re.search('(\d+)',txt_clean)
        if rex:
            return int(rex.group(1))
        else:
            return None
    else:
        return None

group_labels = ['Single','2-5','6-50','50-200','200-2,000','2,000+']
def groupify(nb):
    x = get_built(nb)
    if x == None:
        return 0
    elif x == 1:
        return 1
    elif x <=5:
        return 2
    elif x <=50:
        return 3
    elif x <=200:
        return 4
    elif x <=2_000:
        return 5
    else:
        return 6

def yearify(row):
    for val in (f"{row['first flight']}{row.introduced}{row.introduction}", str(row.category)):
        x = re.findall('((?:19|20)\d\d)', str(val))
        if x:
            v = min([int(n) for n in x])
            if v < 2020 and v > 1899:
                return v
    return None


def to_df(data):
    fulldataset = pd.DataFrame.from_records(list(data.values()))
    
    fulldataset = fulldataset.assign(built_group=fulldataset['number built'].apply(groupify))\
                             .assign(built_number=fulldataset['number built'].apply(get_built).values)\
                             .assign(views=fulldataset.views.apply(lambda x: float(x) if x != 'NA' else None))\
                             .assign(year= fulldataset.apply(yearify,axis=1))  
    
    ticon = lambda term: fulldataset.title.str.contains(term, regex=False, na=True)
    return fulldataset.loc[(~fulldataset.built_number.isnull()) &
                          (fulldataset.built_group != 0) & 
                          (~fulldataset.views.isnull()) &
                          (~ticon('Category:')) & 
                          (~ticon('Squadron')) & 
                          (~ticon('Division')) & 
                          (~ticon('Bomber Wing')) & 
                          (~ticon('Fighter Wing')) & 
                          (~ticon('Group'))]
mil_df = to_df(military)
civ_df = to_df(civil)

In [187]:
vio_traces = []
scatter_traces = []
pivot_traces = []
import re

for side, label, dataset, color, dark_color in (("negative", "civil", civ_df, "teal","blue"), ("positive", "military", mil_df, "coral","red")):    
    trace = {
                "type": 'violin',
                "x": dataset.built_group,
                "y": dataset.views,
                "name": label,
                "text": dataset.title,
                "side": side,
                "box": {
                    "visible": True
                },
                "meanline": {
                    "visible": True
                },
                'spanmode': 'hard',
                "line": {
                    "color": color
                }
            }
    vio_traces.append(trace)
    
    pivot = Counter(dataset.built_group)
    pivot_trace = go.Scatter(
                mode= 'lines',
                x= list(range(1,7)),
                y= [pivot[k] for k in range(1,7)],
                name= f'N in bin ({label})',
                text= correct_order,
                yaxis='y2',
                line={'color': color}
            )
    pivot_traces.append(pivot_trace)
    
    scatter_traces.append(go.Scatter(
            x = dataset.built_number+np.random.random_sample(size=len(dataset.built_number))/3,
            y = dataset.views,
            text = dataset.title,
            name = label,
            mode = 'markers',
            marker= {'opacity':0.2, 'color': dark_color}
            ))

iplot({'data': traces, #+pivot_traces
       'layout':{'title': 'Plane population vs. popularity',
                 'yaxis':{'title':'Daily views on Wiki page'},
                 'yaxis2': {
                    'overlaying': 'y', 'range': [0,600],
                    'side': 'right'},
                 'xaxis': {'ticktext': group_labels,
                 'tickvals': list(range(1,1+len(group_labels)))},
                 "violingap": 0,
                 "violinmode": "overlay"
                }
      })                
        
iplot({'data': traces, #+pivot_traces
       'layout':{'title': 'Plane population vs. popularity',
                 'yaxis':{'title':'Daily views on Wiki page', 'type': 'log'},
                 'yaxis2': {
                    'overlaying': 'y', 'range': [0,600],
                    'side': 'right'},
                 'xaxis': {'ticktext': group_labels,
                 'tickvals': list(range(1,1+len(group_labels)))},
                 "violingap": 0,
                 "violinmode": "overlay"
                }
      })  


iplot({'data':scatter_traces,
       'layout':{'title': 'Planes: population vs. popularity','xaxis':{'title':'Numbers built', 'type': 'log'},'yaxis':{'title':'Daily views on en.wiki', 'type': 'log'}}
      })

So the B1 bomber is a curious case. The infobox has two numbers, the first 5 units for the B1A, the second 100 units for the B1B. Therefore this shows how its not overly reliable...

In [288]:
scatter_traces = []
for label, dataset, dark_color in (("civil", civ_df, "teal"), ("military", mil_df, "coral")):
    df = dataset.loc[~dataset.year.isnull()].loc[~dataset.views.isnull()]
    scatter_traces.append(go.Scattergl(
                x = df.year,
                y = df.views,
                text = dataset.title,
                name = label,
                mode = 'markers',
                marker= {'opacity':0.2,
                         'color': dark_color,
                        'size': np.log2(df.built_number.values + 1),
                         'sizeref': 1.3,
                        'sizemin':0.2}
                ))
    
    
scale = np.array(range(4,13)) #73000.0
scatter_traces.append(go.Scattergl(
                            x = [1915+8*n for n in scale],
                            y = [0.3]*len(scale),
                            text = [str(2**n) for n in scale],
                            textposition='bottom center',
                            name = 'scale',
                            mode = 'markers+text',
                            marker= {'opacity':0.5,
                                     'color': 'darkorchid',
                                    'size': scale,
                                     'sizeref': 1.3,
                                    'sizemin':0.2}
                            ))   


iplot({'data':scatter_traces,
       'layout':{'title': 'Planes: Numbers built, year of introduction and wikipedia pagevisits',
                 'xaxis':{'title':'Numbers built'},
                 'yaxis':{'title':'Daily views on en.wiki', 'type': 'log'},
                'shapes': [{
                            'type': 'rect',
                            'x0': 1939,
                            'y0': 0.1,
                            'x1': 1945,
                            'y1': 1e4,
                            'line': {
                            'width': 0,
                            },
                            'fillcolor': 'rgba(10, 10, 10, 0.1)',
                            },
                            {
                            'type': 'rect',
                            'x0': 1914,
                            'y0': 0.1,
                            'x1': 1918,
                            'y1': 1e4,
                            'line': {
                            'width': 0,
                            },
                            'fillcolor': 'rgba(10, 10, 10, 0.1)',
                            }
                          ]}
      })

In [246]:
# worst mil
mil_df.sort_values(['views'])

category  \
5149   Category:1910s German fighter aircraft|Categor...   
11118                 Category:Mexican military aircraft   
1300   Category:Military aircraft of World War I|Cate...   
3798   Category:1920s German military reconnaissance ...   
5055   Category:1920s German fighter aircraft|Categor...   
5056   Category:1920s German fighter aircraft|Categor...   
3110   Category:1930s French military trainer aircraf...   
1301   Category:Military aircraft of World War I|Cate...   
5111   Category:1910s German fighter aircraft|Categor...   
3799   Category:1920s German military reconnaissance ...   
3920   Category:1930s French military reconnaissance ...   
3141   Category:1920s French military trainer aircraf...   
3695   Category:1920s Japanese military reconnaissanc...   
3136   Category:1920s French military trainer aircraf...   
3800   Category:1920s German military reconnaissance ...   
1383   Category:Military aircraft of World War I|Cate...   
6431   Category:1920s Czechoslovakian fighter aircraf...   
3919   Category:1930s French military reconnaissance ...   
3139   Category:1920s French military trainer aircraf...   
1670   Category:1910s German military utility aircraf...   
3117   Category:1920s French military trainer aircraf...   
3191   Category:1920s Czechoslovakian military traine...   
3753   Category:1910s international military reconnai...   
4029   Category:1920s Czechoslovakian military reconn...   
5322   Category:1910s French fighter aircraft|Categor...   
3790   Category:1920s German military reconnaissance ...   
1293   Category:Military aircraft of World War I|Cate...   
4433   Category:Fighter aircraft|Category:Fighter air...   
3611   Category:1920s Soviet and Russian military rec...   
3142   Category:1920s French military trainer aircraf...   
...                                                  ...   
2350   Category:1980s United States military transpor...   
6462   Category:2010s Chinese fighter aircraft|Catego...   
344    Category:United States military helicopters|Ca...   
1045   Category:World War II bombers of the United St...   
4727   Category:1980s Swedish fighter aircraft|Catego...   
1044   Category:World War II bombers of the United St...   
4763   Category:2000s Russian fighter aircraft|Catego...   
6554   Category:1930s British fighter aircraft|Catego...   
3517   Category:1950s United States military reconnai...   
387    Category:United States military helicopters|Ca...   
333    Category:Attack helicopters|Category:United St...   
4781   Category:1970s Soviet fighter aircraft|Categor...   
4552   Category:1940s United States fighter aircraft|...   
6901   Category:1970s United States bomber aircraft|C...   
2363   Category:1950s United States military transpor...   
2347   Category:1990s United States military transpor...   
4507   Category:1950s United States fighter aircraft|...   
4476   Category:1970s United States fighter aircraft|...   
5007   Category:2000s Indian fighter aircraft|Categor...   
5002   Category:1990s international fighter aircraft|...   
5175   Category:1970s French fighter aircraft|Categor...   
7508   Category:1970s United States attack aircraft|C...   
4762   Category:2010s Russian fighter aircraft|Catego...   
4474   Category:1970s United States fighter aircraft|...   
6899   Category:1980s United States bomber aircraft|C...   
6911   Category:1950s United States bomber aircraft|C...   
5172   Category:1980s French fighter aircraft|Categor...   
4465   Category:1990s United States fighter aircraft|...   
3504   Category:1960s United States military reconnai...   
4477   Category:1970s United States fighter aircraft|...   

                      first flight         introduced          introduction  \
5149                  October 1917                                    Error   
11118                 June 1, 1980              Error                 Error   
1300                          1917                                    Error   
3798       

In [247]:
#worst
civ_df.sort_values(['views'])

category  \
3101  Category:1950s Polish civil utility aircraft|C...   
5312  Category:1930s French sport aircraft|Category:...   
4510  Category:German sailplanes|Category:German sai...   
5592        Category:1910s French experimental aircraft   
5056  Category:1930s French civil utility aircraft|C...   
5987  Category:1930s Czechoslovakian sport aircraft|...   
4829        Category:1910s German experimental aircraft   
4830        Category:1910s German experimental aircraft   
4512  Category:German sailplanes|Category:German sai...   
5516  Category:1930s French civil trainer aircraft|C...   
5572        Category:1930s French experimental aircraft   
5571        Category:1930s French experimental aircraft   
5057  Category:1930s French civil utility aircraft|C...   
2757  Category:1920s Soviet and Russian military rec...   
2250  Category:1940s United States special-purpose a...   
5543        Category:1940s French experimental aircraft   
2758  Category:1920s Soviet and Russian military rec...   
3912  Category:1920s Italian civil trainer aircraft|...   
2759  Category:1920s Soviet and Russian military rec...   
3939       Category:1910s Italian experimental aircraft   
8280  Category:1940s Soviet military transport aircr...   
4847  Category:1920s German cargo aircraft|Category:...   
5481  Category:1920s French sailplanes|Category:1920...   
2248  Category:1940s United States special-purpose a...   
3829  Category:1950s Italian sailplanes|Category:195...   
3423                    Category:Mexican civil aircraft   
2756  Category:1920s Soviet and Russian military rec...   
3527      Category:1930s Japanese experimental aircraft   
2831  Category:1920s Soviet and Russian civil aircra...   
5042  Category:1940s French civil utility aircraft|C...   
...                                                 ...   
6211  Category:1960s Canadian civil utility aircraft...   
2139  Category:1980s United States special-purpose a...   
2627  Category:1960s Soviet civil utility aircraft|C...   
6326  Category:1990s Canadian business aircraft|Cate...   
2811  Category:1970s Soviet cargo aircraft|Category:...   
8195  Category:1990s United States military transpor...   
2394  Category:1990s Swiss civil utility aircraft|Ca...   
8324  Category:2000s international military transpor...   
8004                             Category:NASA aircraft   
2780  Category:1960s Soviet military reconnaissance ...   
386   Category:1970s United States civil utility air...   
2217  Category:1950s United States helicopters|Categ...   
7890  Category:Racing aircraft|Category:Racing aircraft   
2859  Category:1970s Soviet helicopters|Category:197...   
4028  Category:1990s international cargo aircraft|Ca...   
4027  Category:2010s international cargo aircraft|Ca...   
1848  Category:1950s United States experimental airc...   
8224  Category:1940s United States military transpor...   
2868  Category:1960s Soviet helicopters|Category:196...   
8202  Category:1960s United States military transpor...   
8199  Category:1980s United States military transpor...   
2157  Category:1970s United States helicopters|Categ...   
2808  Category:1980s Soviet cargo aircraft|Category:...   
2195  Category:1960s United States helicopters|Categ...   
2162  Category:1970s United States helicopters|Categ...   
1966  Category:1980s United States cargo aircraft|Ca...   
8209  Category:1950s United States military transpor...   
8197  Category:1990s United States military transpor...   
1963  Category:2000s United States cargo aircraft|Ca...   
8008                             Category:NASA aircraft   

                  first flight                                   introduced  \
3101         17 May 1951 (S-3)                                        Error   
5312                      1936                                        Error   
4510                                                                          
5592                                                                    

In [249]:
# top mil
mil_df.sort_values(['views'],ascending=False)

category  \
4477   Category:1970s United States fighter aircraft|...   
3504   Category:1960s United States military reconnai...   
4465   Category:1990s United States fighter aircraft|...   
5172   Category:1980s French fighter aircraft|Categor...   
6911   Category:1950s United States bomber aircraft|C...   
6899   Category:1980s United States bomber aircraft|C...   
4474   Category:1970s United States fighter aircraft|...   
4762   Category:2010s Russian fighter aircraft|Catego...   
7508   Category:1970s United States attack aircraft|C...   
5175   Category:1970s French fighter aircraft|Categor...   
5002   Category:1990s international fighter aircraft|...   
5007   Category:2000s Indian fighter aircraft|Categor...   
4476   Category:1970s United States fighter aircraft|...   
4507   Category:1950s United States fighter aircraft|...   
2347   Category:1990s United States military transpor...   
2363   Category:1950s United States military transpor...   
6901   Category:1970s United States bomber aircraft|C...   
4552   Category:1940s United States fighter aircraft|...   
4781   Category:1970s Soviet fighter aircraft|Categor...   
333    Category:Attack helicopters|Category:United St...   
387    Category:United States military helicopters|Ca...   
3517   Category:1950s United States military reconnai...   
6554   Category:1930s British fighter aircraft|Catego...   
4763   Category:2000s Russian fighter aircraft|Catego...   
1044   Category:World War II bombers of the United St...   
4727   Category:1980s Swedish fighter aircraft|Catego...   
1045   Category:World War II bombers of the United St...   
344    Category:United States military helicopters|Ca...   
6462   Category:2010s Chinese fighter aircraft|Catego...   
2350   Category:1980s United States military transpor...   
...                                                  ...   
3142   Category:1920s French military trainer aircraf...   
3611   Category:1920s Soviet and Russian military rec...   
4433   Category:Fighter aircraft|Category:Fighter air...   
1293   Category:Military aircraft of World War I|Cate...   
3790   Category:1920s German military reconnaissance ...   
5322   Category:1910s French fighter aircraft|Categor...   
4029   Category:1920s Czechoslovakian military reconn...   
3753   Category:1910s international military reconnai...   
3191   Category:1920s Czechoslovakian military traine...   
3117   Category:1920s French military trainer aircraf...   
1670   Category:1910s German military utility aircraf...   
3139   Category:1920s French military trainer aircraf...   
3919   Category:1930s French military reconnaissance ...   
6431   Category:1920s Czechoslovakian fighter aircraf...   
1383   Category:Military aircraft of World War I|Cate...   
3800   Category:1920s German military reconnaissance ...   
3136   Category:1920s French military trainer aircraf...   
3695   Category:1920s Japanese military reconnaissanc...   
3141   Category:1920s French military trainer aircraf...   
3920   Category:1930s French military reconnaissance ...   
3799   Category:1920s German military reconnaissance ...   
5111   Category:1910s German fighter aircraft|Categor...   
1301   Category:Military aircraft of World War I|Cate...   
3110   Category:1930s French military trainer aircraf...   
5056   Category:1920s German fighter aircraft|Categor...   
5055   Category:1920s German fighter aircraft|Categor...   
3798   Category:1920s German military reconnaissance ...   
1300   Category:Military aircraft of World War I|Cate...   
11118                 Category:Mexican military aircraft   
5149   Category:1910s German fighter aircraft|Categor...   

                      first flight         introduced          introduction  \
4477   20 January 1974 (unplanned)     17 August 1978                 Error   
3504              22 December 1964       January 1966                 Error   
4465              7 September 1997   15 December 2005                 Error   
5172   Rafa

In [289]:
# top civ
civ_df.sort_values(['built_number'],ascending=False)

category  \
2210  Category:1950s United States special-purpose a...   
416   Category:1960s United States civil utility air...   
489   Category:1950s United States civil utility air...   
485   Category:1950s United States civil utility air...   
601   Category:1930s United States civil utility air...   
2641  Category:1940s Soviet civil utility aircraft|C...   
550   Category:1940s United States civil utility air...   
2627  Category:1960s Soviet civil utility aircraft|C...   
2217  Category:1950s United States helicopters|Categ...   
2253  Category:1940s United States special-purpose a...   
507   Category:1940s United States civil utility air...   
1616  Category:1940s United States military gliders|...   
7890  Category:Racing aircraft|Category:Racing aircraft   
2859  Category:1970s Soviet helicopters|Category:197...   
474   Category:1950s United States civil utility air...   
8178  Category:World War II transport aircraft of th...   
484   Category:1950s United States civil utility air...   
651   Category:1930s United States civil utility air...   
443   Category:1960s United States civil utility air...   
413   Category:1960s United States civil utility air...   
544   Category:1940s United States civil utility air...   
378   Category:1970s United States civil utility air...   
450   Category:1960s United States civil utility air...   
2755  Category:1920s Soviet and Russian military rec...   
150   Category:United States civil aircraft|Category...   
473   Category:1950s United States civil utility air...   
455   Category:1960s United States civil utility air...   
486   Category:1950s United States civil utility air...   
8139  Category:World War II Soviet transport aircraf...   
1039  Category:1970s United States civil trainer air...   
...                                                 ...   
5600        Category:1910s French experimental aircraft   
5619        Category:1900s French experimental aircraft   
8522  Category:Abandoned civil aircraft projects of ...   
5606        Category:1900s French experimental aircraft   
5605        Category:1900s French experimental aircraft   
5618        Category:1900s French experimental aircraft   
5617        Category:1900s French experimental aircraft   
5612  Category:1900s French experimental aircraft|Ca...   
5608        Category:1900s French experimental aircraft   
8433                  Category:Supersonic business jets   
8508  Category:Abandoned civil aircraft projects of ...   
8502  Category:Abandoned civil aircraft projects of ...   
1642  Category:1940s United States military gliders|...   
8490  Category:Abandoned civil aircraft projects of ...   
3526  Category:1940s Japanese experimental aircraft|...   
1960  Category:United States cargo aircraft|Category...   
8481         Category:Abandoned civil aircraft projects   
8474         Category:Abandoned civil aircraft projects   
4797        Category:1940s German experimental aircraft   
8473         Category:Abandoned civil aircraft projects   
2788  Category:1930s Soviet military reconnaissance ...   
4801        Category:1940s German experimental aircraft   
2251  Category:1940s United States special-purpose a...   
8334        Category:German military transport aircraft   
1623  Category:1940s United States military gliders|...   
8461         Category:Abandoned civil aircraft projects   
4874  Category:1940s German helicopters|Category:194...   
8456         Category:Abandoned civil aircraft projects   
4873  Category:1940s German helicopters|Category:194...   
8462         Category:Abandoned civil aircraft projects   

                        first flight                   introduced  \
2210                                                                
416                  14 January 1960           [[1960 in aviation   
489               September 12, 1957                                
485                                                          1956   
601                             1938       

In [295]:
civ_df.loc[civ_df.built_number < 100].sort_values(['views'],ascending=False)

category  \
8008                             Category:NASA aircraft   
2808  Category:1980s Soviet cargo aircraft|Category:...   
8224  Category:1940s United States military transpor...   
1848  Category:1950s United States experimental airc...   
4027  Category:2010s international cargo aircraft|Ca...   
4028  Category:1990s international cargo aircraft|Ca...   
8004                             Category:NASA aircraft   
8324  Category:2000s international military transpor...   
2139  Category:1980s United States special-purpose a...   
2809  Category:1980s Soviet cargo aircraft|Category:...   
2117  Category:2000s United States helicopters|Categ...   
2854  Category:1980s Soviet helicopters|Category:198...   
2104  Category:2000s United States civil aircraft|Ca...   
8325  Category:2000s international military transpor...   
1935  Category:1900s United States experimental airc...   
1962  Category:2000s United States cargo aircraft|Ca...   
2005  Category:2000s United States business aircraft...   
8007                             Category:NASA aircraft   
1870  Category:1940s United States experimental airc...   
8196  Category:1990s United States military transpor...   
3510            Category:Japanese experimental aircraft   
1685  Category:2010s United States experimental airc...   
4103  Category:2010s Indian helicopters|Category:201...   
1719  Category:2000s United States experimental airc...   
2300  Category:1920s United States special-purpose a...   
8204  Category:1960s United States military transpor...   
2114  Category:2000s United States helicopters|Categ...   
8194  Category:2000s United States military transpor...   
2441  Category:2010s Swiss business aircraft|Categor...   
8416         Category:2010s military transport aircraft   
...                                                 ...   
3527      Category:1930s Japanese experimental aircraft   
2756  Category:1920s Soviet and Russian military rec...   
3423                    Category:Mexican civil aircraft   
3829  Category:1950s Italian sailplanes|Category:195...   
2248  Category:1940s United States special-purpose a...   
2251  Category:1940s United States special-purpose a...   
5481  Category:1920s French sailplanes|Category:1920...   
4847  Category:1920s German cargo aircraft|Category:...   
8280  Category:1940s Soviet military transport aircr...   
3939       Category:1910s Italian experimental aircraft   
1623  Category:1940s United States military gliders|...   
2759  Category:1920s Soviet and Russian military rec...   
3912  Category:1920s Italian civil trainer aircraft|...   
2758  Category:1920s Soviet and Russian military rec...   
5543        Category:1940s French experimental aircraft   
2250  Category:1940s United States special-purpose a...   
2757  Category:1920s Soviet and Russian military rec...   
5057  Category:1930s French civil utility aircraft|C...   
5571        Category:1930s French experimental aircraft   
5572        Category:1930s French experimental aircraft   
5516  Category:1930s French civil trainer aircraft|C...   
4512  Category:German sailplanes|Category:German sai...   
4830        Category:1910s German experimental aircraft   
4829        Category:1910s German experimental aircraft   
5987  Category:1930s Czechoslovakian sport aircraft|...   
5056  Category:1930s French civil utility aircraft|C...   
5592        Category:1910s French experimental aircraft   
4510  Category:German sailplanes|Category:German sai...   
5312  Category:1930s French sport aircraft|Category:...   
3101  Category:1950s Polish civil utility aircraft|C...   

                      first flight         introduced    introduction  ns  \
8008              22 December 1964       January 1966           Error   0   
2808              21 December 1988                              Error   0   
8224              November 2, 1947                              Error   0   
1848                   8 June 1959  17 September 1959           Error   0   
402

In [299]:
civ_df.loc[civ_df.built_number >= 1].sort_values(['views'],ascending=False)

category  \
8008                             Category:NASA aircraft   
1963  Category:2000s United States cargo aircraft|Ca...   
8197  Category:1990s United States military transpor...   
8209  Category:1950s United States military transpor...   
1966  Category:1980s United States cargo aircraft|Ca...   
2162  Category:1970s United States helicopters|Categ...   
2195  Category:1960s United States helicopters|Categ...   
2808  Category:1980s Soviet cargo aircraft|Category:...   
2157  Category:1970s United States helicopters|Categ...   
8199  Category:1980s United States military transpor...   
8202  Category:1960s United States military transpor...   
2868  Category:1960s Soviet helicopters|Category:196...   
8224  Category:1940s United States military transpor...   
1848  Category:1950s United States experimental airc...   
4027  Category:2010s international cargo aircraft|Ca...   
4028  Category:1990s international cargo aircraft|Ca...   
2859  Category:1970s Soviet helicopters|Category:197...   
7890  Category:Racing aircraft|Category:Racing aircraft   
2217  Category:1950s United States helicopters|Categ...   
386   Category:1970s United States civil utility air...   
2780  Category:1960s Soviet military reconnaissance ...   
8004                             Category:NASA aircraft   
8324  Category:2000s international military transpor...   
2394  Category:1990s Swiss civil utility aircraft|Ca...   
8195  Category:1990s United States military transpor...   
2811  Category:1970s Soviet cargo aircraft|Category:...   
6326  Category:1990s Canadian business aircraft|Cate...   
2627  Category:1960s Soviet civil utility aircraft|C...   
2139  Category:1980s United States special-purpose a...   
6211  Category:1960s Canadian civil utility aircraft...   
...                                                 ...   
5042  Category:1940s French civil utility aircraft|C...   
2831  Category:1920s Soviet and Russian civil aircra...   
3527      Category:1930s Japanese experimental aircraft   
2756  Category:1920s Soviet and Russian military rec...   
3423                    Category:Mexican civil aircraft   
3829  Category:1950s Italian sailplanes|Category:195...   
2248  Category:1940s United States special-purpose a...   
5481  Category:1920s French sailplanes|Category:1920...   
4847  Category:1920s German cargo aircraft|Category:...   
8280  Category:1940s Soviet military transport aircr...   
3939       Category:1910s Italian experimental aircraft   
2759  Category:1920s Soviet and Russian military rec...   
3912  Category:1920s Italian civil trainer aircraft|...   
2758  Category:1920s Soviet and Russian military rec...   
5543        Category:1940s French experimental aircraft   
2250  Category:1940s United States special-purpose a...   
2757  Category:1920s Soviet and Russian military rec...   
5057  Category:1930s French civil utility aircraft|C...   
5571        Category:1930s French experimental aircraft   
5572        Category:1930s French experimental aircraft   
5516  Category:1930s French civil trainer aircraft|C...   
4512  Category:German sailplanes|Category:German sai...   
4830        Category:1910s German experimental aircraft   
4829        Category:1910s German experimental aircraft   
5987  Category:1930s Czechoslovakian sport aircraft|...   
5056  Category:1930s French civil utility aircraft|C...   
5592        Category:1910s French experimental aircraft   
4510  Category:German sailplanes|Category:German sai...   
5312  Category:1930s French sport aircraft|Category:...   
3101  Category:1950s Polish civil utility aircraft|C...   

                  first flight                                   introduced  \
8008          22 December 1964                                 January 1966   
1963  747-8F: February 8, 2010  747-8F: October 12, 2011, with [[Cargolux]]   
8197         15 September 1991                              17 January 1995   
8209            23 August 1954                                December 1

In [297]:
mil_df.loc[mil_df.built_number == 0].sort_values(['views'],ascending=False)

category first flight  \
7757   Category:Carrier-based aircraft|Category:Carri...        Error   
1154   Category:Boeing B-29 Superfortress|Category:Bo...                
10976  Category:Cancelled military aircraft projects ...                
11215  Category:Abandoned military aircraft projects ...                
7765   Category:Carrier-based aircraft|Category:Carri...                
7137   Category:1940s German bomber aircraft|Category...                
11224  Category:Abandoned military aircraft projects ...                
6508   Category:1950s British fighter aircraft|Catego...                
10965  Category:Cancelled military aircraft projects ...                
6859   Category:Bomber aircraft|Category:Bomber aircr...                
11226  Category:Abandoned military aircraft projects ...         none   
10979  Category:Cancelled military aircraft projects ...          n/a   
818    Category:World War II dive bombers|Category:Wo...                
6860   Category:Bomber aircraft|Category:Bomber aircr...                
11231  Category:Abandoned military aircraft projects ...                
6738   Category:1980s Argentine fighter aircraft|Cate...        Error   
10975  Category:Cancelled military aircraft projects ...          n/a   
11238  Category:Abandoned military aircraft projects ...        Error   
11094  Category:Abandoned military aircraft projects ...                
6482   Category:1950s Canadian fighter aircraft|Categ...                
744    Category:World War II jet aircraft of Germany|...                
10967  Category:Cancelled military aircraft projects ...                
10944  Category:Cancelled military aircraft projects ...                
11101  Category:Abandoned military aircraft projects ...                
740    Category:World War II jet aircraft of Japan|Ca...                
11210  Category:Abandoned military aircraft projects ...                
11061  Category:Unmanned aerial vehicles of the Sovie...                
10970  Category:Cancelled military aircraft projects ...          n/a   
756    Category:World War II jet aircraft of Germany|...                
10980  Category:Cancelled military aircraft projects ...                
...                                                  ...          ...   
10938  Category:Cancelled military aircraft projects ...                
10915  Category:Unmanned aerial vehicles of the Unite...                
220    Category:World War II helicopters of Germany|C...         1942   
10960  Category:Cancelled military aircraft projects ...                
2814   Category:1970s Spanish military trainer aircra...                
6968   Category:1920s United States bomber aircraft|C...                
6981   Category:1920s United States bomber aircraft|C...                
1547   Category:1940s United States military utility ...                
10989  Category:Cancelled military aircraft projects ...                
6976   Category:1920s United States bomber aircraft|C...                
6977   Category:1920s United States bomber aircraft|C...                
924    Category:World War II Japanese fighter aircraf...                
2225   Category:Unmanned military aircraft of the Uni...                
11013  Category:Abandoned military aircraft engine pr...        Error   
11304  Category:Abandoned military aircraft projects ...                
1844   Category:Target drones|Category:Target drones|...        Error   
3645   Category:1930s Polish military reconnaissance ...                
10969  Category:Cancelled military aircraft projects ...                
3270   Category:1940s British military trainer aircra...                
3633   Category:1930s Soviet military reconnaissance ...                
6972   Category:1920s United States bomber aircraft|C...                
925    Category:World War II Japanese fighter aircraf...                
1291   Category:Military aircraft of World War I|Cate...                
438    Category:1940s United Stat

In [298]:
mil_df.loc[mil_df.built_number == 1].sort_values(['views'],ascending=False)

category  \
2379   Category:1940s United States military transpor...   
4769   Category:1990s Soviet and Russian fighter airc...   
4768   Category:1990s Soviet and Russian fighter airc...   
4910   Category:2010s Japanese fighter aircraft|Categ...   
4461   Category:2010s United States fighter aircraft|...   
11017                  Category:Boeing military aircraft   
4765   Category:2000s Russian fighter aircraft|Catego...   
5174   Category:1970s French fighter aircraft|Categor...   
2512   Category:1940s German military transport aircr...   
2410   Category:Ukrainian military transport aircraft...   
10344  Category:1990s United States military aircraft...   
6932   Category:1940s United States bomber aircraft|C...   
2456   Category:1940s Soviet military transport aircr...   
2430   Category:2010s Russian military transport airc...   
6910   Category:1950s United States bomber aircraft|C...   
6964   Category:1930s United States bomber aircraft|C...   
369    Category:United States military helicopters|Ca...   
411    Category:1990s United States military gliders|...   
2386   Category:1940s United States military transpor...   
1822   Category:Unmanned military aircraft|Category:U...   
7015   Category:1950s Soviet bomber aircraft|Category...   
11095  Category:Abandoned military aircraft projects ...   
10920  Category:Unmanned aerial vehicles of the Unite...   
4472   Category:1970s United States fighter aircraft|...   
958    Category:World War II fighter aircraft of Germ...   
7581   Category:1940s Soviet attack aircraft|Category...   
391    Category:United States military helicopters|Ca...   
349    Category:United States military helicopters|Ca...   
4560   Category:1940s United States fighter aircraft|...   
2240   Category:Unmanned military aircraft of the Uni...   
...                                                  ...   
3613   Category:1920s Soviet and Russian military rec...   
3140   Category:1920s French military trainer aircraf...   
5204   Category:1930s French fighter aircraft|Categor...   
7227   Category:1930s French bomber aircraft|Category...   
4432   Category:Fighter aircraft|Category:Fighter air...   
7094   Category:1920s Italian bomber aircraft|Categor...   
3612   Category:1920s Soviet and Russian military rec...   
5107   Category:1910s German fighter aircraft|Categor...   
4437   Category:Fighter aircraft|Category:Fighter air...   
10887  Category:Unmanned aerial vehicles of the Unite...   
4431   Category:Fighter aircraft|Category:Fighter air...   
3142   Category:1920s French military trainer aircraf...   
3611   Category:1920s Soviet and Russian military rec...   
4433   Category:Fighter aircraft|Category:Fighter air...   
1293   Category:Military aircraft of World War I|Cate...   
4029   Category:1920s Czechoslovakian military reconn...   
3191   Category:1920s Czechoslovakian military traine...   
3919   Category:1930s French military reconnaissance ...   
6431   Category:1920s Czechoslovakian fighter aircraf...   
1383   Category:Military aircraft of World War I|Cate...   
3800   Category:1920s German military reconnaissance ...   
3136   Category:1920s French military trainer aircraf...   
3141   Category:1920s French military trainer aircraf...   
3920   Category:1930s French military reconnaissance ...   
3799   Category:1920s German military reconnaissance ...   
3110   Category:1930s French military trainer aircraf...   
5056   Category:1920s German fighter aircraft|Categor...   
5055   Category:1920s German fighter aircraft|Categor...   
1300   Category:Military aircraft of World War I|Cate...   
5149   Category:1910s German fighter aircraft|Categor...   

                             first flight   introduced introduction  ns  \
2379                     November 2, 1947                     Error   0   
4769                         2 April 1996                     Error   0   
4768                    25 September 1997                     Error   0   
4910                       